In [1]:
import math, random
import torch
import torchaudio
from torchaudio import transforms
from IPython.display import Audio

In [2]:
class AudioUtil():
  # ----------------------------
  # Load an audio file. Return the signal as a tensor and the sample rate
  # ----------------------------
  @staticmethod
  def open(audio_file):
    sig, sr = torchaudio.load(audio_file)
    return (sig, sr)

  @staticmethod
  def rechannel(aud, new_channel):
    sig, sr = aud

    if (sig.shape[0] == new_channel):
      # Nothing to do
      return aud

    if (new_channel == 1):
      # Convert from stereo to mono by selecting only the first channel
      resig = sig[:1, :]
    else:
      # Convert from mono to stereo by duplicating the first channel
      resig = torch.cat([sig, sig])

    return ((resig, sr))

  @staticmethod
  def resample(aud, newsr):
    sig, sr = aud

    if (sr == newsr):
      # Nothing to do
      return aud

    num_channels = sig.shape[0]
    # Resample first channel
    resig = torchaudio.transforms.Resample(sr, newsr)(sig[:1,:])
    if (num_channels > 1):
      # Resample the second channel and merge both channels
      retwo = torchaudio.transforms.Resample(sr, newsr)(sig[1:,:])
      resig = torch.cat([resig, retwo])

    return ((resig, newsr))

  @staticmethod
  def pad_trunc(aud, max_ms):
    sig, sr = aud
    num_rows, sig_len = sig.shape
    max_len = sr//1000 * max_ms

    if (sig_len > max_len):
      # Truncate the signal to the given length
      sig = sig[:,:max_len]

    elif (sig_len < max_len):
      # Length of padding to add at the beginning and end of the signal
      pad_begin_len = random.randint(0, max_len - sig_len)
      pad_end_len = max_len - sig_len - pad_begin_len

      # Pad with 0s
      pad_begin = torch.zeros((num_rows, pad_begin_len))
      pad_end = torch.zeros((num_rows, pad_end_len))

      sig = torch.cat((pad_begin, sig, pad_end), 1)
      
    return (sig, sr)

  @staticmethod
  def time_shift(aud, shift_limit):
    sig,sr = aud
    _, sig_len = sig.shape
    shift_amt = int(random.random() * shift_limit * sig_len)
    return (sig.roll(shift_amt), sr)

  @staticmethod
  def spectro_gram(aud, n_mels=64, n_fft=1024, hop_len=None):
    sig,sr = aud
    top_db = 80

    # spec has shape [channel, n_mels, time], where channel is mono, stereo etc
    spec = torchaudio.transforms.MelSpectrogram(sr, n_fft=n_fft, hop_length=hop_len, n_mels=n_mels)(sig)

    # Convert to decibels
    spec = torchaudio.transforms.AmplitudeToDB(top_db=top_db)(spec)
    return (spec)

  @staticmethod
  def spectro_augment(spec, max_mask_pct=0.1, n_freq_masks=1, n_time_masks=1):
    _, n_mels, n_steps = spec.shape
    mask_value = spec.mean()
    aug_spec = spec

    freq_mask_param = max_mask_pct * n_mels
    for _ in range(n_freq_masks):
      aug_spec = torchaudio.transforms.FrequencyMasking(freq_mask_param)(aug_spec, mask_value)

    time_mask_param = max_mask_pct * n_steps
    for _ in range(n_time_masks):
      aug_spec = torchaudio.transforms.TimeMasking(time_mask_param)(aug_spec, mask_value)

    return aug_spec

In [3]:
from torch.utils.data import DataLoader, Dataset, random_split
import torchaudio

# ----------------------------
# Sound Dataset
# ----------------------------
class SoundDS(Dataset):
  def __init__(self, df, data_path):
    self.df = df
    self.data_path = str(data_path)
    self.duration = 20000
    self.sr = 44100
    self.channel = 2
    self.shift_pct = 0.4
            
  # ----------------------------
  # Number of items in dataset
  # ----------------------------
  def __len__(self):
    return len(self.df)    
    
  # ----------------------------
  # Get i'th item in dataset
  # ----------------------------
  def __getitem__(self, idx):
    # Absolute file path of the audio file - concatenate the audio directory with
    # the relative path
    audio_file = self.data_path + "/smalldata" + "/wavs" + self.df.loc[idx, 'folder'] + "/"+ self.df.loc[idx, 'fileName']
    # Get the Class ID
    labels = {
        "acousticness" : self.df.loc[idx, 'acousticness'],
        "danceability" : self.df.loc[idx, 'danceability'],
        "energy" : self.df.loc[idx, 'energy'],
        "instrumentalness" : self.df.loc[idx, 'instrumentalness'],
        "liveness" : self.df.loc[idx, 'liveness'],
        "speechiness" : self.df.loc[idx, 'speechiness'],
        "tempo" : self.df.loc[idx, 'tempo'],
        "valence" : self.df.loc[idx, 'valence']
    }


    aud = AudioUtil.open(audio_file)
    # Some sounds have a higher sample rate, or fewer channels compared to the
    # majority. So make all sounds have the same number of channels and same 
    # sample rate. Unless the sample rate is the same, the pad_trunc will still
    # result in arrays of different lengths, even though the sound duration is
    # the same.
    reaud = AudioUtil.resample(aud, self.sr)
    rechan = AudioUtil.rechannel(reaud, self.channel)

    dur_aud = AudioUtil.pad_trunc(rechan, self.duration)
    shift_aud = AudioUtil.time_shift(dur_aud, self.shift_pct)
    sgram = AudioUtil.spectro_gram(shift_aud, n_mels=64, n_fft=1024, hop_len=None)
    aug_sgram = AudioUtil.spectro_augment(sgram, max_mask_pct=0.1, n_freq_masks=2, n_time_masks=2)

    return [aug_sgram, labels]

  def getSpectro(self,idx):
    audio_file = self.data_path + "/smalldata" + "/wavs" + self.df.loc[idx, 'folder'] + "/"+ self.df.loc[idx, 'fileName']
    aud = AudioUtil.open(audio_file)
    # Some sounds have a higher sample rate, or fewer channels compared to the
    # majority. So make all sounds have the same number of channels and same 
    # sample rate. Unless the sample rate is the same, the pad_trunc will still
    # result in arrays of different lengths, even though the sound duration is
    # the same.
    reaud = AudioUtil.resample(aud, self.sr)
    rechan = AudioUtil.rechannel(reaud, self.channel)

    dur_aud = AudioUtil.pad_trunc(rechan, self.duration)
    shift_aud = AudioUtil.time_shift(dur_aud, self.shift_pct)
    sgram = AudioUtil.spectro_gram(shift_aud, n_mels=64, n_fft=1024, hop_len=None)
    aug_sgram = AudioUtil.spectro_augment(sgram, max_mask_pct=0.1, n_freq_masks=2, n_time_masks=2)
    return aug_sgram

In [4]:
from torch.utils.data import DataLoader, Dataset, random_split
import torchaudio

# ----------------------------
# Sound Dataset
# ----------------------------
class SoundDS_NewData(Dataset):
  def __init__(self, df, data_path):
    self.df = df
    self.data_path = str(data_path)
    self.duration = 10000
    self.sr = 44100
    self.channel = 2
    self.shift_pct = 0.4
            
  # ----------------------------
  # Number of items in dataset
  # ----------------------------
  def __len__(self):
    return len(self.df)    
    
  def __getitem__(self, idx):
    audio_file = self.data_path + "/smalldata" + "/wavs" + self.df.loc[idx, 'folder'] + "/"+ self.df.loc[idx, 'fileName']
    aud = ''
    try:
        aud = AudioUtil.open(audio_file)
    except:
        audio_file = self.data_path + "/smalldata" + "/wavs" + "/000" + "/"+ "000002.wav"
        aud = AudioUtil.open(audio_file)
        
    aud = AudioUtil.open(audio_file)
    # Some sounds have a higher sample rate, or fewer channels compared to the
    # majority. So make all sounds have the same number of channels and same 
    # sample rate. Unless the sample rate is the same, the pad_trunc will still
    # result in arrays of different lengths, even though the sound duration is
    # the same.
    reaud = AudioUtil.resample(aud, self.sr)
    rechan = AudioUtil.rechannel(reaud, self.channel)

    dur_aud = AudioUtil.pad_trunc(rechan, self.duration)
    shift_aud = AudioUtil.time_shift(dur_aud, self.shift_pct)
    sgram = AudioUtil.spectro_gram(shift_aud, n_mels=64, n_fft=1024, hop_len=None)
    aug_sgram = AudioUtil.spectro_augment(sgram, max_mask_pct=0.1, n_freq_masks=2, n_time_masks=2)
    return aug_sgram, f"{self.df.loc[idx,'song_name']} by {self.df.loc[idx,'artist']}"

  def getName(self,idx):
        return self.df.loc[idx,"song_name"], self.df.loc[idx,"artist"]

In [7]:
import pandas as pd
datafile = pd.read_csv("./spotify_data3.csv")
# datafile = datafile.loc[datafile["folder"] == "/000"]
datafile.head()
len(datafile)

13123

In [8]:
from torch.utils.data import random_split

myds = SoundDS(datafile, ".")

In [9]:
num_items = len(myds)
num_train = round(num_items * 0.8)
num_val = num_items - num_train
train_ds, val_ds = random_split(myds, [num_train, num_val])
num_items
# myds.__getitem__(13122)

13123

In [11]:
len(val_ds)

2625

In [263]:
batch_size = 64

In [264]:
train_dl = torch.utils.data.DataLoader(train_ds, batch_size=batch_size, shuffle=True)
val_dl = torch.utils.data.DataLoader(val_ds, batch_size=batch_size, shuffle=False)

In [228]:
acousticDict = {"0": 0.0, "1" : 0.1, "2": 0.2, "3": 0.3, "4": 0.4, "5": 0.5, "6": 0.6, "7": 0.7, "8": 0.8, "9": 0.9, "10": 1.0}
danceabilityDict = {"0": 0.0, "1": 0.1, "2": 0.2, "3": 0.3, "4": 0.4, "5": 0.5, "6": 0.6, "7": 0.7, "8": 0.8, "9": 0.9, "10": 1.0}
energyDict = {"0": 0.0, "1": 0.1, "2": 0.2, "3": 0.3, "4": 0.4, "5": 0.5, "6": 0.6, "7": 0.7, "8": 0.8, "9": 0.9, "10": 1.0}
instrumentalnessDict = {"0": 0.0, "1": 0.1, "2": 0.2, "3": 0.3, "4": 0.4, "5": 0.5, "6": 0.6, "7": 0.7, "8": 0.8, "9": 0.9, "10": 1.0}
livenessDict = {"0": 0.0, "1": 0.1, "2": 0.2, "3": 0.3, "4": 0.4, "5": 0.5, "6": 0.6, "7": 0.7, "8": 0.8, "9": 0.9, "10": 1.0}
speechinessDict = {"0": 0.0, "1": 0.1, "2": 0.2, "3": 0.3, "4": 0.4, "5": 0.5, "6": 0.6, "7": 0.7, "8": 0.8, "9": 0.9, "10": 1.0}
valenceDict = {"0": 0.0, "1": 0.1, "2": 0.2, "3": 0.3, "4": 0.4, "5": 0.5, "6": 0.6, "7": 0.7, "8": 0.8, "9": 0.9, "10": 1.0}
tempo = {}
for i in range(250):
    tempo[f"{i}"] = i

In [690]:
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import time
from torchvision import datasets, transforms, models
from torch.nn import init

In [299]:
class MultilabelClassifier(nn.Module):
    def __init__(self):
        super().__init__()
    
        conv_layers = []

        # First Convolution Block with Relu and Batch Norm. Use Kaiming Initialization
        self.conv1 = nn.Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
        self.relu1 = nn.ReLU()
        self.bn1 = nn.BatchNorm2d(8)
        init.kaiming_normal_(self.conv1.weight, a=0.1)
        self.conv1.bias.data.zero_()
        conv_layers += [self.conv1, self.relu1, self.bn1]

        # Second Convolution Block
        self.conv2 = nn.Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
        self.relu2 = nn.ReLU()
        self.bn2 = nn.BatchNorm2d(16)
        init.kaiming_normal_(self.conv2.weight, a=0.1)
        self.conv2.bias.data.zero_()
        conv_layers += [self.conv2, self.relu2, self.bn2]

        # Second Convolution Block
        self.conv3 = nn.Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
        self.relu3 = nn.ReLU()
        self.bn3 = nn.BatchNorm2d(32)
        init.kaiming_normal_(self.conv3.weight, a=0.1)
        self.conv3.bias.data.zero_()
        conv_layers += [self.conv3, self.relu3, self.bn3]

        # Second Convolution Block
        self.conv4 = nn.Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
        self.relu4 = nn.ReLU()
        self.bn4 = nn.BatchNorm2d(64)
        init.kaiming_normal_(self.conv4.weight, a=0.1)
        self.conv4.bias.data.zero_()
        conv_layers += [self.conv4, self.relu4, self.bn4]
        
        self.conv = nn.Sequential(*conv_layers)
        self.ap = nn.AdaptiveAvgPool2d(output_size=1)
        self.sig = nn.Sigmoid()
        self.lin = nn.Linear(in_features=64, out_features=7)

        
    def forward(self, x):

        x = self.conv(x)
        x = self.ap(x)
        x = x.view(x.shape[0], -1)
        x = self.lin(x)
#         x = self.lin2(x)
#         x = self.lin3(x)
        x = self.sig(x)
#         print(x.shape)
        
        return x

In [300]:
labelList = ["acousticness", "danceability", "energy",
             "instrumentalness", "liveness", "speechiness", "valence"]
def extractLabels(labels, index):
    newLabels = []
    for label in labelList:
        newLabels.append(labels[label][index])
    return torch.Tensor(newLabels)

In [398]:

def criterion(loss_func,outputs,labels):
  losses = 0
  lossList = []
  for i, key in enumerate(outputs):
#     print("len labels = ", len(extractLabels(labels,i)) )
#     print("len otput[i] = ", len( outputs[i]) )
#     print("labels: ",extractLabels(labels,i))
#     print("output: ", outputs[i])
    newLoss = loss_func(outputs[i], (extractLabels(labels,i)).to(device))
#     print("loss: ",newLoss)
    losses += newLoss
    lossList.append(newLoss)
#     losses += loss_func(outputs[i], 
#               ((labels[labelList[i]]).type(torch.LongTensor)).to(device))
  return [losses,lossList]

In [399]:
def training(model,device,lr_rate,epochs,train_loader):
  num_epochs = epochs
  losses = []
  checkpoint_losses = []

  optimizer = torch.optim.Adam(model.parameters(), lr=lr_rate)
  n_total_steps = len(train_loader)

  loss_func = nn.CrossEntropyLoss()
#   loss_func = nn.MSELoss

  for epoch in range(num_epochs):
     for i, data in enumerate(train_loader):
        inputs = data[0].to(device)
        labels = data[1]

        # Normalize the inputs
        inputs_m, inputs_s = inputs.mean(), inputs.std()
        inputs = (inputs - inputs_m) / inputs_s
        
        optimizer.zero_grad()

        outputs = model(inputs)

        loss = criterion(loss_func, outputs, labels)[0]
        losses.append(loss.item())

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        if (i+1) % (int(n_total_steps/1)) == 0:
            checkpoint_loss = torch.tensor(losses).mean().item()
            checkpoint_losses.append(checkpoint_loss)
            print (f'Epoch [{epoch+1}/{num_epochs}], Step [{i+1}/{n_total_steps}], Loss: {checkpoint_loss:.4f}')
  return checkpoint_losses

In [407]:
def checkAccuracy(model, testloader, criterion, loss_func,batch_size):
    totalLosses = [0,0,0,0,0,0,0]
    testLen = len(testloader)
    with torch.no_grad():
        for data in testloader:
            inputs = data[0].to(device)
            labels = data[1]
            
            inputs_m, inputs_s = inputs.mean(), inputs.std()
            inputs = (inputs - inputs_m) / inputs_s
            
            outputs = model(inputs)
            lossList = criterion(loss_func, outputs, labels)[1]
            
            
            for i in range(len(lossList)):
                totalLosses[i%7] += lossList[i] 
    totalLoss = 0
    print("End of epoch validation losses...:")
    for index, loss in enumerate(totalLosses):
        print(f"{labelList[index]} loss: {(loss/testLen):.2f}")
        totalLoss += loss
    
    print(f"Average total loss: {totalLoss/testLen:.2f}")
    return totalLosses        

In [424]:
def training2(model, train_dl, num_epochs, batch_size):
  # Loss Function, Optimizer and Scheduler
#   criterion = nn.CrossEntropyLoss()
#   loss_func = nn.CrossEntropyLoss()
  lossList = []
  labelLosses = [[],[],[],[],[],[],[]]
  loss_func = nn.MSELoss() 
#   optimizer = torch.optim.Adam(model.parameters(),lr=0.005)
  optimizer = torch.optim.SGD(model.parameters(),lr=0.005)
  scheduler = torch.optim.lr_scheduler.OneCycleLR(optimizer, max_lr=0.005,
                                                steps_per_epoch=int(len(train_dl)),
                                                epochs=num_epochs,
                                                anneal_strategy='linear')

  # Repeat for each epoch
  for epoch in range(num_epochs):
    print(f"Epoch {epoch}")
    running_loss = 0.0
    correct_prediction = 0
    total_prediction = 0
    count = 1

    # Repeat for each batch in the training set
    for i, data in enumerate(train_dl):
        # Get the input features and target labels, and put them on the GPU
        inputs = data[0].to(device)
        labels = data[1]

        # Normalize the inputs
        inputs_m, inputs_s = inputs.mean(), inputs.std()
        inputs = (inputs - inputs_m) / inputs_s

        # Zero the parameter gradients
        optimizer.zero_grad()

        # forward + backward + optimize
        outputs = model(inputs)
#         print(outputs)
        loss = criterion(loss_func, outputs, labels)[0]
        
#         loss = loss_func(outputs,labels)
        loss.backward()
        optimizer.step()
        scheduler.step()

        # Keep stats for Loss and Accuracy
        running_loss += loss.item()
    
        if count % 30 == 0:
            print(f"average loss: {running_loss / count}")
        count += 1

    
    # Print stats at the end of the epoch
    num_batches = len(train_dl)
    avg_loss = running_loss / num_batches
    lossList.append(avg_loss)
    separateLosses = checkAccuracy(model, val_dl, criterion, loss_func, batch_size)
    for ind,loss in enumerate(separateLosses):
        labelLosses[ind].append(loss)
#     acc = correct_prediction/total_prediction
#     print(f'Epoch: {epoch}, Loss: {avg_loss:.2f}, Accuracy: {acc:.2f}')

  print('Finished Training')
  return lossList, separateLosses

In [425]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# device = "cpu"

device 

device(type='cuda')

In [427]:
modelFinale2 = MultilabelClassifier()
modelFinale2.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [430]:
for param in modelFinale2.parameters():
    if len(param.shape) > 1: # Initialize only the weight tensors
        init.normal_(param, mean=0, std=0.01)

In [431]:
start = time.time()
epochs = 5
averageLosses, separateLosses = training2(modelFinale2, train_dl, 3, batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 6.523805634180705
average loss: 5.489678764343262
average loss: 4.833121795124478
average loss: 4.468333411216736
average loss: 4.237885862986246
End of epoch validation losses...:
acousticness loss: 0.50
danceability loss: 0.43
energy loss: 0.44
instrumentalness loss: 0.43
liveness loss: 0.44
speechiness loss: 0.43
valence loss: 0.40
Average total loss: 3.07
Epoch 1
average loss: 3.141201543807983
average loss: 3.1188626170158384
average loss: 3.0855477200614083
average loss: 3.0652604679266613
average loss: 3.0476166645685834
End of epoch validation losses...:
acousticness loss: 0.45
danceability loss: 0.38
energy loss: 0.40
instrumentalness loss: 0.40
liveness loss: 0.42
speechiness loss: 0.40
valence loss: 0.37
Average total loss: 2.82
Epoch 2
average loss: 2.9233943859736127
average loss: 2.890669310092926
average loss: 2.862364739841885
average loss: 2.8683715124924976
average loss: 2.8457012669245403
End of epoch validation losses...:
acousticness loss: 0.4

In [414]:
modelFinale = MultilabelClassifier()
modelFinale.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [415]:
start = time.time()
epochs = 5
averageLosses, separateLosses = training2(modelFinale, train_dl, 5, batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 6.411480458577474
average loss: 5.932156125704448
average loss: 5.4403713358773125
average loss: 4.956944215297699
average loss: 4.571863066355387
End of epoch validation losses...:
acousticness loss: 0.47
danceability loss: 0.42
energy loss: 0.42
instrumentalness loss: 0.41
liveness loss: 0.43
speechiness loss: 0.40
valence loss: 0.39
Average total loss: 2.95
Epoch 1
average loss: 2.998306703567505
average loss: 2.9782835364341738
average loss: 2.936781716346741
average loss: 2.8901377856731414
average loss: 2.869297563234965
End of epoch validation losses...:
acousticness loss: 0.41
danceability loss: 0.36
energy loss: 0.38
instrumentalness loss: 0.37
liveness loss: 0.37
speechiness loss: 0.37
valence loss: 0.36
Average total loss: 2.63
Epoch 2
average loss: 2.710949985186259
average loss: 2.6827095627784727
average loss: 2.6767201821009317
average loss: 2.6477932105461757
average loss: 2.6436170077323915
End of epoch validation losses...:
acousticness loss: 0.4

In [416]:
torch.save(modelFinale.state_dict(), "./final.pt")

In [417]:
batch_size = 32# choose an appropriate batch size
new_loader = DataLoader(toBeLabeledData, batch_size=batch_size)

# Evaluate the model on the new set of spectrograms
modelFinale.eval()
with torch.no_grad():
    for batch in val_dl:
        inputs = batch[0].to(device)
        outputs = modelFinale(inputs)
        for i in range(batch_size):
            print("guess:",outputs[i])
            print("label:",extractLabels(batch[1],i))
#         print(outputs)
#         print(batch[1])

guess: tensor([1.7908e-16, 9.9462e-01, 1.0000e+00, 1.0000e+00, 5.8061e-01, 9.9921e-01,
        5.7743e-09], device='cuda:0')
label: tensor([0.7451, 0.6919, 0.4925, 0.8498, 0.1258, 0.0856, 0.8678])
guess: tensor([7.1825e-09, 3.5001e-01, 1.0000e+00, 1.0000e+00, 9.9946e-01, 9.9990e-01,
        2.4636e-10], device='cuda:0')
label: tensor([0.0021, 0.4327, 0.8246, 0.1568, 0.7232, 0.0538, 0.2460])
guess: tensor([1.0000e+00, 4.1300e-03, 9.9982e-01, 1.0000e+00, 5.0836e-01, 6.9262e-02,
        4.2028e-08], device='cuda:0')
label: tensor([0.7301, 0.4057, 0.3299, 0.9117, 0.2025, 0.0616, 0.0422])
guess: tensor([1.7805e-07, 7.7593e-01, 1.0000e+00, 1.0000e+00, 1.2630e-01, 3.4860e-02,
        2.2203e-03], device='cuda:0')
label: tensor([0.0118, 0.3882, 0.9073, 0.9266, 0.2879, 0.0380, 0.9061])
guess: tensor([1.5667e-02, 9.7962e-01, 1.0000e+00, 1.0000e+00, 7.0395e-01, 9.6169e-01,
        1.5341e-05], device='cuda:0')
label: tensor([0.0145, 0.6382, 0.7145, 0.3847, 0.1367, 0.0292, 0.5496])
guess: tensor([

KeyboardInterrupt: 

In [366]:
modelSGDLR2 = MultilabelClassifier()
modelSGDLR2.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [367]:
start = time.time()
epochs = 5
training2(modelSGDLR2, train_dl, 1, batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
len labels =  7
len otput[i] =  7
labels:  tensor([0.3132, 0.4223, 0.6460, 0.8445, 0.1646, 0.0280, 0.9194])
output:  tensor([0.5163, 0.5191, 0.4576, 0.4416, 0.5274, 0.5026, 0.4271],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1211, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.4824, 0.0830, 0.5390, 0.9215, 0.7600, 0.0453, 0.3913])
output:  tensor([0.4155, 0.5175, 0.4045, 0.5023, 0.4730, 0.5327, 0.4630],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1017, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.2397, 0.5904, 0.6970, 0.9353, 0.1113, 0.0293, 0.3429])
output:  tensor([0.5046, 0.4999, 0.5195, 0.5213, 0.5409, 0.4972, 0.4920],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1010, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([9.9580e-01, 2.9346e-01, 1.1847e-01, 2.598

output:  tensor([0.4368, 0.5464, 0.3907, 0.4612, 0.4814, 0.5425, 0.4709],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1730, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.0572, 0.4606, 0.0799, 0.9096, 0.1138, 0.0549, 0.0374])
output:  tensor([0.4899, 0.5192, 0.5488, 0.5385, 0.4467, 0.5476, 0.4446],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1525, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.9771, 0.4655, 0.4215, 0.9169, 0.0864, 0.0310, 0.8278])
output:  tensor([0.4718, 0.5430, 0.4659, 0.4679, 0.5571, 0.5298, 0.4497],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1540, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([7.9585e-01, 3.3334e-01, 3.1172e-01, 6.8400e-08, 5.9705e-02, 3.6649e-02,
        1.3334e-01])
output:  tensor([0.4120, 0.4961, 0.4319, 0.4378, 0.5355, 0.4633,

loss:  tensor(0.1394, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.9936, 0.2611, 0.0354, 0.8659, 0.6835, 0.0474, 0.1491])
output:  tensor([0.6570, 0.5856, 0.4946, 0.5123, 0.5002, 0.4486, 0.4530],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1202, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.0195, 0.6015, 0.8618, 0.0119, 0.6076, 0.0558, 0.8424])
output:  tensor([0.4350, 0.5286, 0.5654, 0.5189, 0.5136, 0.5290, 0.4240],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1329, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.0721, 0.6047, 0.7915, 0.5922, 0.1128, 0.0446, 0.6917])
output:  tensor([0.4655, 0.5177, 0.4172, 0.4781, 0.5123, 0.5229, 0.4912],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1063, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7

loss:  tensor(0.1192, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.2271, 0.4960, 0.3286, 0.5443, 0.0889, 0.0299, 0.0832])
output:  tensor([0.4852, 0.5371, 0.5269, 0.4861, 0.5201, 0.5110, 0.4585],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.0956, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.7420, 0.1431, 0.9456, 0.7152, 0.1320, 0.0583, 0.1232])
output:  tensor([0.4680, 0.5518, 0.3977, 0.4371, 0.5191, 0.6117, 0.4974],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1737, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.5173, 0.5540, 0.8971, 0.0021, 0.0647, 0.0420, 0.7263])
output:  tensor([0.4664, 0.4875, 0.4537, 0.4723, 0.4977, 0.5324, 0.4967],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1294, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7

len labels =  7
len otput[i] =  7
labels:  tensor([0.0023, 0.8492, 0.4651, 0.9323, 0.0762, 0.0446, 0.8614])
output:  tensor([0.4811, 0.4895, 0.4949, 0.4915, 0.5632, 0.4957, 0.4517],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1661, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.0502, 0.6753, 0.5491, 0.8695, 0.0724, 0.1228, 0.3990])
output:  tensor([0.4619, 0.5114, 0.4388, 0.4794, 0.5362, 0.5489, 0.4884],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.1093, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.1236, 0.6187, 0.7535, 0.0015, 0.5139, 0.1292, 0.5696])
output:  tensor([0.4686, 0.5260, 0.4685, 0.5070, 0.5507, 0.5178, 0.4814],
       device='cuda:0', grad_fn=<SelectBackward0>)
loss:  tensor(0.0892, device='cuda:0', grad_fn=<MseLossBackward0>)
len labels =  7
len otput[i] =  7
labels:  tensor([0.3205, 0.7357, 0.6871, 0.1819, 0.0714, 0.0353, 0

...

loss:  tensor(0.0931, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.1506, 0.7495, 0.9719, 0.8149, 0.2708, 0.1117, 0.7180])
output:  tensor([0.1992, 0.4189, 0.8289, 0.6602, 0.2094, 0.1182, 0.4125],
       device='cuda:0')
loss:  tensor(0.0362, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.0155, 0.7184, 0.7811, 0.8726, 0.2743, 0.0276, 0.3489])
output:  tensor([0.1387, 0.4993, 0.8186, 0.6107, 0.2168, 0.1212, 0.4968],
       device='cuda:0')
loss:  tensor(0.0239, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([9.2916e-01, 1.6154e-01, 5.9011e-05, 9.4965e-01, 9.1073e-02, 1.2253e-01,
        2.9741e-02])
output:  tensor([0.8600, 0.3673, 0.2484, 0.7067, 0.1731, 0.1093, 0.3223],
       device='cuda:0')
loss:  tensor(0.0372, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.0095, 0.5467, 0.8068, 0.0023, 0.0945, 0.0503, 0.5302])
output:  tensor([0.2968, 0.3803, 0.7268, 0.7132, 0.1867, 0.1020, 0.3774],
       d

loss:  tensor(0.0469, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([5.7686e-04, 2.1979e-01, 9.5444e-01, 8.0835e-01, 1.3429e-01, 1.0603e-01,
        4.5508e-01])
output:  tensor([0.2745, 0.3991, 0.7573, 0.6647, 0.1904, 0.0993, 0.3924],
       device='cuda:0')
loss:  tensor(0.0248, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.0043, 0.3181, 0.9916, 0.0043, 0.2375, 0.1146, 0.0540])
output:  tensor([0.8003, 0.3572, 0.5772, 0.6512, 0.2042, 0.0814, 0.4243],
       device='cuda:0')
loss:  tensor(0.1950, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.9943, 0.5707, 0.3721, 0.9727, 0.0922, 0.0425, 0.0376])
output:  tensor([0.6712, 0.3955, 0.4542, 0.7746, 0.1509, 0.0875, 0.3109],
       device='cuda:0')
loss:  tensor(0.0373, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.9942, 0.5101, 0.5806, 0.9655, 0.4602, 0.0886, 0.0669])
output:  tensor([0.7361, 0.5192, 0.3166, 0.6499, 0.2232, 0.1850, 0.5081],
       d

output:  tensor([0.6813, 0.4820, 0.4023, 0.6728, 0.1501, 0.0854, 0.4000],
       device='cuda:0')
loss:  tensor(0.0906, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.7084, 0.2704, 0.5700, 0.9699, 0.1133, 0.0349, 0.0851])
output:  tensor([0.8676, 0.2851, 0.4839, 0.7576, 0.1543, 0.0615, 0.2882],
       device='cuda:0')
loss:  tensor(0.0174, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.4617, 0.2916, 0.2516, 0.8804, 0.1324, 0.0376, 0.1216])
output:  tensor([0.2807, 0.5213, 0.5677, 0.7141, 0.1689, 0.0933, 0.4272],
       device='cuda:0')
loss:  tensor(0.0444, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.1179, 0.8322, 0.4958, 0.8649, 0.1102, 0.0809, 0.5520])
output:  tensor([0.3240, 0.5700, 0.5813, 0.6809, 0.1744, 0.1150, 0.4923],
       device='cuda:0')
loss:  tensor(0.0230, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.0562, 0.4203, 0.8553, 0.9123, 0.0555, 0.0317, 0.1735])
output:  tensor([0.3

labels:  tensor([0.6158, 0.7963, 0.3255, 0.8875, 0.1153, 0.0637, 0.6403])
output:  tensor([0.4380, 0.6626, 0.4779, 0.6050, 0.1829, 0.1254, 0.5142],
       device='cuda:0')
loss:  tensor(0.0253, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.5349, 0.4626, 0.3844, 0.8934, 0.1016, 0.0441, 0.1365])
output:  tensor([0.4427, 0.5168, 0.5724, 0.6952, 0.1537, 0.0798, 0.4362],
       device='cuda:0')
loss:  tensor(0.0257, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.4207, 0.3419, 0.5297, 0.9385, 0.1996, 0.0424, 0.1174])
output:  tensor([0.3132, 0.3912, 0.7509, 0.6418, 0.1984, 0.0974, 0.4193],
       device='cuda:0')
loss:  tensor(0.0350, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.0075, 0.7594, 0.5163, 0.9230, 0.2038, 0.1063, 0.4220])
output:  tensor([0.4898, 0.6471, 0.5054, 0.5144, 0.1841, 0.1328, 0.6130],
       device='cuda:0')
loss:  tensor(0.0643, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.9

loss:  tensor(0.0302, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.8345, 0.5693, 0.2948, 0.0454, 0.7521, 0.0667, 0.8006])
output:  tensor([0.5740, 0.5657, 0.4696, 0.5617, 0.1868, 0.1220, 0.5222],
       device='cuda:0')
loss:  tensor(0.1093, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.9599, 0.2913, 0.8010, 0.9641, 0.1143, 0.0701, 0.0429])
output:  tensor([0.7075, 0.3579, 0.5563, 0.6521, 0.1775, 0.0961, 0.3619],
       device='cuda:0')
loss:  tensor(0.0474, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.2102, 0.7061, 0.5114, 0.8537, 0.2784, 0.0329, 0.3049])
output:  tensor([0.3444, 0.6177, 0.4029, 0.7576, 0.1432, 0.1061, 0.3620],
       device='cuda:0')
loss:  tensor(0.0105, device='cuda:0')
len labels =  7
len otput[i] =  7
labels:  tensor([0.1685, 0.4961, 0.3394, 0.7696, 0.2494, 0.0476, 0.5292])
output:  tensor([0.5359, 0.4795, 0.5380, 0.6478, 0.1848, 0.1081, 0.4336],
       device='cuda:0')
loss:  tensor(0.0295

In [330]:
modelSGDLR = MultilabelClassifier()
modelSGDLR.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [331]:
start = time.time()
epochs = 5
training2(modelSGDLR, train_dl, 5, batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 6.507816326618195
average loss: 5.369981145858764
average loss: 4.785802811384201
average loss: 4.425922434031963
acousticness loss: 0.52
danceability loss: 0.45
energy loss: 0.45
instrumentalness loss: 0.44
liveness loss: 0.46
speechiness loss: 0.46
valence loss: 0.42
Average loss: 3.20
Epoch 1
average loss: 3.307794749736786
average loss: 3.2608783155679704
average loss: 3.2362954556941985
average loss: 3.204338525235653
acousticness loss: 0.48
danceability loss: 0.42
energy loss: 0.43
instrumentalness loss: 0.42
liveness loss: 0.44
speechiness loss: 0.41
valence loss: 0.40
Average loss: 3.00
Epoch 2
average loss: 3.1190743505954743
average loss: 3.038457578420639
average loss: 3.035413517554601
average loss: 3.0184851229190826
acousticness loss: 0.46
danceability loss: 0.40
energy loss: 0.41
instrumentalness loss: 0.40
liveness loss: 0.42
speechiness loss: 0.41
valence loss: 0.39
Average loss: 2.89
Epoch 3
average loss: 2.974479979276657
average loss: 2.9347055

In [306]:
modelMoreLR = MultilabelClassifier()
modelMoreLR.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [307]:
start = time.time()
epochs = 5
training2(modelMoreLR, train_dl, 3, batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 6.47125391960144
average loss: 5.629506242275238
average loss: 4.840286892652512
average loss: 4.399884702265263
acousticness loss: 0.48
danceability loss: 0.40
energy loss: 0.42
instrumentalness loss: 0.42
liveness loss: 0.42
speechiness loss: 0.40
valence loss: 0.39
Average loss: 2.93
Epoch 1
average loss: 2.934494560956955
average loss: 2.8896665394306185
average loss: 2.8390700856844586
average loss: 2.8003051400184633
acousticness loss: 0.42
danceability loss: 0.38
energy loss: 0.38
instrumentalness loss: 0.38
liveness loss: 0.38
speechiness loss: 0.37
valence loss: 0.36
Average loss: 2.67
Epoch 2
average loss: 2.697541856765747
average loss: 2.681709146499634
average loss: 2.641622468829155
average loss: 2.6058847688138487
acousticness loss: 0.38
danceability loss: 0.34
energy loss: 0.36
instrumentalness loss: 0.35
liveness loss: 0.34
speechiness loss: 0.34
valence loss: 0.33
Average loss: 2.43
Finished Training
Train time 4125.0666790008545 seconds, 825.013

In [423]:
batch_size = 32# choose an appropriate batch size
new_loader = DataLoader(toBeLabeledData, batch_size=batch_size)

# Evaluate the model on the new set of spectrograms
modelSGDLR.eval()
with torch.no_grad():
    for batch in val_dl:
        inputs = batch[0].to(device)
        outputs = modelSGDLR(inputs)
        for i in range(batch_size):
            print("guess:",outputs[i])
            print("label:",extractLabels(batch[1],i))
#         print(outputs)
#         print(batch[1])

guess: tensor([0.0509, 0.7688, 0.5805, 0.9085, 0.1136, 0.1225, 0.3105],
       device='cuda:0')
label: tensor([0.7451, 0.6919, 0.4925, 0.8498, 0.1258, 0.0856, 0.8678])
guess: tensor([0.5035, 0.4902, 0.6354, 0.5709, 0.0849, 0.0563, 0.1436],
       device='cuda:0')
label: tensor([0.0021, 0.4327, 0.8246, 0.1568, 0.7232, 0.0538, 0.2460])
guess: tensor([0.9827, 0.3927, 0.1470, 0.9902, 0.0477, 0.0231, 0.0760],
       device='cuda:0')
label: tensor([0.7301, 0.4057, 0.3299, 0.9117, 0.2025, 0.0616, 0.0422])
guess: tensor([0.7216, 0.6330, 0.5254, 0.8690, 0.0827, 0.0497, 0.4367],
       device='cuda:0')
label: tensor([0.0118, 0.3882, 0.9073, 0.9266, 0.2879, 0.0380, 0.9061])
guess: tensor([0.8735, 0.6319, 0.7375, 0.5179, 0.1815, 0.2672, 0.5769],
       device='cuda:0')
label: tensor([0.0145, 0.6382, 0.7145, 0.3847, 0.1367, 0.0292, 0.5496])
guess: tensor([0.9833, 0.4327, 0.0486, 0.8703, 0.0850, 0.0976, 0.1762],
       device='cuda:0')
label: tensor([0.9956, 0.4119, 0.1035, 0.9656, 0.0770, 0.0439, 0

KeyboardInterrupt: 

In [ ]:
[0.5089, 0.4934, 0.4833, 0.5658, 0.3435, 0.3011, 0.4650]]
[0.5280, 0.5032, 0.5000, 0.4981, 0.4837, 0.4912, 0.5217]]

In [290]:
modelMoreLayers = MultilabelClassifier()
modelMoreLayers.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [291]:
start = time.time()
epochs = 5
training2(modelMoreLayers, train_dl, 3, batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 6.897604477405548
average loss: 6.305478936433792
average loss: 5.6685918986797335
average loss: 5.094630074501038
acousticness loss: 0.48
danceability loss: 0.42
energy loss: 0.43
instrumentalness loss: 0.42
liveness loss: 0.45
speechiness loss: 0.43
valence loss: 0.42
Average loss: 3.04
Epoch 1
average loss: 3.17913413643837
average loss: 3.1228254795074464
average loss: 3.067784917354584
average loss: 3.034180146455765
acousticness loss: 0.45
danceability loss: 0.38
energy loss: 0.41
instrumentalness loss: 0.39
liveness loss: 0.41
speechiness loss: 0.39
valence loss: 0.38
Average loss: 2.80
Epoch 2
average loss: 2.856695681810379
average loss: 2.8568764239549638


KeyboardInterrupt: 

In [278]:
model = MultilabelClassifier()
model.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [279]:
import time

In [280]:
start = time.time()
epochs = 5
training2(model, train_dl, 3, batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 0.11293088812381029
average loss: 0.10601233821362258
average loss: 0.1004203526303172
average loss: 0.09295552968978882
acousticness loss: 0.57
danceability loss: 0.50
energy loss: 0.51
instrumentalness loss: 0.50
liveness loss: 0.51
speechiness loss: 0.51
valence loss: 0.48
Average loss: 3.57
Epoch 1
average loss: 0.052786702662706374
average loss: 0.05130268591456115
average loss: 0.050571791796634596
average loss: 0.049697867361828685
acousticness loss: 0.45
danceability loss: 0.40
energy loss: 0.41
instrumentalness loss: 0.40
liveness loss: 0.42
speechiness loss: 0.41
valence loss: 0.39
Average loss: 2.89
Epoch 2
average loss: 0.04661548780277371
average loss: 0.04642805797047913
average loss: 0.04622978841265043
average loss: 0.04630036554299295
acousticness loss: 0.45
danceability loss: 0.39
energy loss: 0.40
instrumentalness loss: 0.40
liveness loss: 0.41
speechiness loss: 0.40
valence loss: 0.37
Average loss: 2.82
Finished Training
Train time 4051.7000648

In [ ]:
#training(model, device, 0.001, 2, train_dl)

In [164]:
model2 = MultilabelClassifier()
model2.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [165]:
start = time.time()
epochs = 5
training2(model2, train_dl, 3,batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 0.108964903652668
average loss: 0.1027186818420887
average loss: 0.09726419902096192
average loss: 0.09044033079408109
acousticness loss: 0.01
danceability loss: 0.01
energy loss: 0.01
instrumentalness loss: 0.01
liveness loss: 0.01
speechiness loss: 0.01
valence loss: 0.01
Average loss: 0.06
Epoch 1
average loss: 0.05588214611634612
average loss: 0.05390318823046982
average loss: 0.05264179725199938
average loss: 0.051857108669355514
acousticness loss: 0.01
danceability loss: 0.01
energy loss: 0.01
instrumentalness loss: 0.01
liveness loss: 0.01
speechiness loss: 0.01
valence loss: 0.01
Average loss: 0.05
Epoch 2
average loss: 0.04965486526489258
average loss: 0.049170148512348535
average loss: 0.04884137135619918
average loss: 0.048574045207351445
acousticness loss: 0.01
danceability loss: 0.01
energy loss: 0.01
instrumentalness loss: 0.01
liveness loss: 0.01
speechiness loss: 0.01
valence loss: 0.01
Average loss: 0.05
Finished Training
Train time 1123.020496368

In [247]:
torch.save(model2.state_dict(), "./mse3.pt")

In [168]:
start = time.time()
epochs = 5
training2(model2, train_dl, 5,batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 0.04863426648080349
average loss: 0.047295431001111866
average loss: 0.047831756776819626
average loss: 0.047983313398435715
acousticness loss: 0.01
danceability loss: 0.01
energy loss: 0.01
instrumentalness loss: 0.01
liveness loss: 0.01
speechiness loss: 0.01
valence loss: 0.01
Average loss: 0.05
Epoch 1
average loss: 0.04723782381042838
average loss: 0.04730176976881921
average loss: 0.04728270306562384
average loss: 0.04722315892577171
acousticness loss: 0.01
danceability loss: 0.01
energy loss: 0.01
instrumentalness loss: 0.01
liveness loss: 0.01
speechiness loss: 0.01
valence loss: 0.01
Average loss: 0.05
Epoch 2
average loss: 0.04691378735005856
average loss: 0.046353789325803516
average loss: 0.04597317818552256
average loss: 0.04586833214852959
acousticness loss: 0.01
danceability loss: 0.01
energy loss: 0.01
instrumentalness loss: 0.01
liveness loss: 0.01
speechiness loss: 0.01
valence loss: 0.01
Average loss: 0.04
Epoch 3
average loss: 0.045190654881298

In [242]:
start = time.time()
epochs = 5
training2(model2, train_dl, 2, batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 0.04370927382260561
average loss: 0.04437635503709316
average loss: 0.04464876937369506
average loss: 0.044752048491500315
acousticness loss: 0.01
danceability loss: 0.01
energy loss: 0.01
instrumentalness loss: 0.01
liveness loss: 0.01
speechiness loss: 0.01
valence loss: 0.01
Average loss: 0.04
Epoch 1
average loss: 0.04484733622521162
average loss: 0.04456243747845292
average loss: 0.04428432133669655
average loss: 0.04419455979950726
acousticness loss: 0.01
danceability loss: 0.01
energy loss: 0.01
instrumentalness loss: 0.01
liveness loss: 0.01
speechiness loss: 0.01
valence loss: 0.01
Average loss: 0.04
Finished Training
Train time 1559.198213815689 seconds, 311.8396427631378 per epoch


In [298]:
with torch.no_grad():
    d = (val_ds[3][0]).unsqueeze(0)
    print(d.shape)
    output = modelMoreLayers(d.to(device))
    print(output)
        
    print(val_ds[2][0])


torch.Size([1, 2, 64, 1719])
tensor([[0.5244, 0.4885, 0.5382, 0.6526, 0.1808, 0.0815, 0.4356]],
       device='cuda:0')
tensor([[[  7.8497,   6.9969,   8.9079,  ...,   8.7589,  10.1137,  11.3289],
         [ 16.9362,  19.2113,  22.9567,  ...,  20.8911,  24.2855,  27.8140],
         [ 24.0604,  24.9446,  26.5424,  ...,  24.8856,  25.9694,  31.5921],
         ...,
         [-32.9033, -32.9033, -32.9033,  ..., -32.9033, -32.9033, -32.9033],
         [-32.9033, -32.9033, -32.9033,  ..., -32.9033, -32.9033, -32.9033],
         [-32.9033, -32.9033, -32.9033,  ..., -32.9033, -32.9033, -32.9033]],

        [[ 25.4756,  10.3245,   3.9496,  ...,  12.5629,  11.1997,  10.2107],
         [ 31.3277,  25.7910,  18.2814,  ...,  24.8400,  23.8563,  25.8615],
         [ 27.9848,  31.1613,  25.7062,  ...,  25.9389,  21.5055,  29.4315],
         ...,
         [-32.9033, -32.9033, -32.9033,  ..., -32.9033, -32.9033, -32.9033],
         [-32.9033, -32.9033, -32.9033,  ..., -32.9033, -32.9033, -32.9033],
   

In [149]:
model3 = MultilabelClassifier()
model3.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [150]:
start = time.time()
epochs = 5
training2(model3, train_dl, 5, batch_size)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0
average loss: 5.657956218719482
average loss: 5.646765744686126
average loss: 5.619418315092722
average loss: 5.60176653265953
acousticness loss: 0.85
danceability loss: 0.76
energy loss: 0.76
instrumentalness loss: 0.76
liveness loss: 0.76
speechiness loss: 0.75
valence loss: 0.76
Average loss: 5.39
Epoch 1
average loss: 5.464208805561066
average loss: 5.41899082660675
average loss: 5.390682844320933
average loss: 5.361174091696739
acousticness loss: 0.81
danceability loss: 0.73
energy loss: 0.73
instrumentalness loss: 0.73
liveness loss: 0.73
speechiness loss: 0.72
valence loss: 0.73
Average loss: 5.19
Epoch 2
average loss: 5.266837430000305
average loss: 5.265875309705734
average loss: 5.2740598320961
average loss: 5.274406424164772
acousticness loss: 0.81
danceability loss: 0.73
energy loss: 0.72
instrumentalness loss: 0.73
liveness loss: 0.73
speechiness loss: 0.72
valence loss: 0.73
Average loss: 5.17
Epoch 3
average loss: 5.227116477489472
average loss: 5.242999559640884

In [163]:
torch.save(model3.state_dict(), "./crossEnt")

In [161]:
with torch.no_grad():
    for i in val_dl:
        data = i[]
    d = (val_ds[0][0]).unsqueeze(0)
    print(d.shape)
    output = model3(d.to(device))
    print(output)
    print(val_ds[0][1])

            

torch.Size([1, 2, 64, 344])
tensor([[0.8132, 0.7911, 0.8265, 0.9452, 0.0252, 0.0106, 0.6579]],
       device='cuda:0')
{'acousticness': 0.552558797, 'danceability': 0.692302488, 'energy': 0.770812011, 'instrumentalness': 0.734063882, 'liveness': 0.110137088, 'speechiness': 0.076767169, 'tempo': 91.759, 'valence': 0.429265827}


In [191]:
def set_parameter_requires_grad(model, feature_extracting):
    if feature_extracting:
        for param in model.parameters():
            param.requires_grad = False

In [192]:
model_ft = models.resnet50(pretrained=True)
# set_parameter_requires_grad(model_ft, False)
num_ftrs = model_ft.fc.in_features
model_ft.fc = nn.Linear(num_ftrs, 8)

C:\Users\merto\anaconda3\lib\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
C:\Users\merto\anaconda3\lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


In [193]:
start = time.time()
epochs = 5
training2(model_ft, train_dl, 3)
finish = time.time()
print(f"Train time {finish-start} seconds, {(finish-start)/epochs} per epoch")

Epoch 0


RuntimeError: Given groups=1, weight of size [64, 3, 7, 7], expected input[8, 2, 64, 344] to have 3 channels, but got 2 channels instead

In [96]:
from operator import add
res_list = list(map(add, [3,1], [4,6]))
res_list

[7, 7]

In [509]:
allSongs = pd.read_csv("./allSongs.csv", low_memory=False)

In [510]:
allSongs["fileName"][52221]

'079999.wav'

In [511]:
allSongs.drop(allSongs.index[52222:allSongs.shape[0]], inplace=True)


In [512]:
allSongs

folder    fileName           song_name                    artist
0       /000  000002.wav                Food                      AWOL
1       /000  000003.wav        Electric Ave                      AWOL
2       /000  000005.wav          This World                      AWOL
3       /000  000010.wav             Freeway                 Kurt Vile
4       /000  000020.wav     Spiritual Level                Nicky Cook
...      ...         ...                 ...                       ...
52217   /079  079994.wav     Old Man's Beard                    Hudson
52218   /079  079995.wav    Two Sun Mountain                    Hudson
52219   /079  079996.wav  Cloches des vaches                   MZ-N710
52220   /079  079998.wav         The Cobbler                    Hudson
52221   /079  079999.wav     Hampi (excerpt)  François-Emmanuel Fodéré

[52222 rows x 4 columns]

In [513]:
toBeLabeledData = SoundDS_NewData(allSongs, ".")

In [514]:
toBeLabeledData[0][1]

'Food by AWOL'

In [515]:
toBeLabeledData.getName(1)

('Electric Ave', 'AWOL')

In [421]:
MSEModel = MultilabelClassifier()
MSEModel.load_state_dict(torch.load("./mse3.pt"))
MSEModel.to(device)

MultilabelClassifier(
  (conv1): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
  (relu1): ReLU()
  (bn1): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv2): Conv2d(8, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu2): ReLU()
  (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv3): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu3): ReLU()
  (bn3): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv4): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
  (relu4): ReLU()
  (bn4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (conv): Sequential(
    (0): Conv2d(2, 8, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU()
    (2): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Conv2d(8, 16, kernel_size=(3, 3), stri

In [422]:
batch_size = 32# choose an appropriate batch size
new_loader = DataLoader(toBeLabeledData, batch_size=batch_size)

# Evaluate the model on the new set of spectrograms
MSEModel.eval()
with torch.no_grad():
    for batch in val_dl:
        inputs = batch[0].to(device)
        outputs = MSEModel(inputs)
        for i in range(batch_size):
            print("guess:",outputs[i])
            print("label:",extractLabels(batch[1],i))
#         print(outputs)
#         print(batch[1])

guess: tensor([0.6899, 0.3764, 0.6601, 0.9584, 0.1365, 0.1130, 0.3446],
       device='cuda:0')
label: tensor([0.7451, 0.6919, 0.4925, 0.8498, 0.1258, 0.0856, 0.8678])
guess: tensor([0.4816, 0.2864, 0.8356, 0.8800, 0.2008, 0.1435, 0.0919],
       device='cuda:0')
label: tensor([0.0021, 0.4327, 0.8246, 0.1568, 0.7232, 0.0538, 0.2460])
guess: tensor([0.9915, 0.1593, 0.1571, 0.9995, 0.1017, 0.0154, 0.1612],
       device='cuda:0')
label: tensor([0.7301, 0.4057, 0.3299, 0.9117, 0.2025, 0.0616, 0.0422])
guess: tensor([0.9522, 0.2175, 0.7185, 0.9933, 0.1340, 0.0638, 0.3708],
       device='cuda:0')
label: tensor([0.0118, 0.3882, 0.9073, 0.9266, 0.2879, 0.0380, 0.9061])
guess: tensor([0.9492, 0.3140, 0.7084, 0.9678, 0.1161, 0.1088, 0.3806],
       device='cuda:0')
label: tensor([0.0145, 0.6382, 0.7145, 0.3847, 0.1367, 0.0292, 0.5496])
guess: tensor([0.9804, 0.2335, 0.0836, 0.9977, 0.0461, 0.0131, 0.2133],
       device='cuda:0')
label: tensor([0.9956, 0.4119, 0.1035, 0.9656, 0.0770, 0.0439, 0

KeyboardInterrupt: 

In [477]:
torch.save(modelSGDLR.state_dict(), "./SGD.pt")

In [516]:
batch_size = 32# choose an appropriate batch size
new_loader = DataLoader(toBeLabeledData, batch_size=batch_size)
allResults = []
# Evaluate the model on the new set of spectrograms
modelSGDLR.eval()
asd = 0
with torch.no_grad():

    for batch in new_loader:

        inputs = batch[0].to(device)
        outputs = modelSGDLR(inputs)
        for i in range(batch_size):
            songInfo = [batch[1][i]]
            for label in outputs[i].tolist():
                songInfo.append(label)
            allResults.append(songInfo)

            asd+=1
        print(len(allResults))

#             print("guess:",outputs[i])
#             print("label:",extractLabels(batch[1],i))
#         print(outputs)
#         print(batch[1])
    

32
64
96
128
160
192
224
256
288
320
352
384
416
448
480
512
544
576
608
640
672
704
736
768
800
832
864
896
928
960
992
1024
1056
1088
1120
1152
1184
1216
1248
1280
1312
1344
1376
1408
1440
1472
1504
1536
1568
1600
1632
1664
1696
1728
1760
1792
1824
1856
1888
1920
1952
1984
2016
2048
2080
2112
2144
2176
2208
2240
2272
2304
2336
2368
2400
2432
2464
2496
2528
2560
2592
2624
2656
2688
2720
2752
2784
2816
2848
2880
2912
2944
2976
3008
3040
3072
3104
3136
3168
3200
3232
3264
3296
3328
3360
3392
3424
3456
3488
3520
3552
3584
3616
3648
3680
3712
3744
3776
3808
3840
3872
3904
3936
3968
4000
4032
4064
4096
4128
4160
4192
4224
4256
4288
4320
4352
4384
4416
4448
4480
4512
4544
4576
4608
4640
4672
4704
4736
4768
4800
4832
4864
4896
4928
4960
4992
5024
5056
5088
5120
5152
5184
5216
5248
5280
5312
5344
5376
5408
5440
5472
5504
5536
5568
5600
5632
5664
5696
5728
5760
5792
5824
5856
5888
5920
5952
5984
6016
6048
6080
6112
6144
6176
6208
6240
6272
6304
6336
6368
6400
6432
6464
6496
6528
6560
6592
6624

45600
45632
45664
45696
45728
45760
45792
45824
45856
45888
45920
45952
45984
46016
46048
46080
46112
46144
46176
46208
46240
46272
46304
46336
46368
46400
46432
46464
46496
46528
46560
46592
46624
46656
46688
46720
46752
46784
46816
46848
46880
46912
46944
46976
47008
47040
47072
47104
47136
47168
47200
47232
47264
47296
47328
47360
47392
47424
47456
47488
47520
47552
47584
47616
47648
47680
47712
47744
47776
47808
47840
47872
47904
47936
47968
48000
48032
48064
48096
48128
48160
48192
48224
48256
48288
48320
48352
48384
48416
48448
48480
48512
48544
48576
48608
48640
48672
48704
48736
48768
48800
48832
48864
48896
48928
48960
48992
49024
49056
49088
49120
49152
49184
49216
49248
49280
49312
49344
49376
49408
49440
49472
49504
49536
49568
49600
49632
49664
49696
49728
49760
49792
49824
49856
49888
49920
49952
49984
50016
50048
50080
50112
50144
50176
50208
50240
50272
50304
50336
50368
50400
50432
50464
50496
50528
50560
50592
50624
50656
50688
50720
50752
50784
50816
50848
50880
5091

IndexError: tuple index out of range

In [517]:
new_df = pd.DataFrame(columns=["song_artist_name","acousticness", 'danceability',
                               "energy", "instrumentalness", "liveness", "speechiness",
                               "valence"], data=allResults)
new_df.to_csv("./allSongLabels.csv", index=False)

In [475]:
len(results)

32

In [519]:
songDataset = pd.read_csv("./allSongsLabelwClusters.csv", low_memory=False)

In [520]:
len(songDataset)

52222

In [705]:
from __future__ import print_function, division
import os
import torch
import pandas as pd
from skimage import io, transform
import numpy as np
import matplotlib.pyplot as plt
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, utils
import torch
from torchvision import transforms, datasets

In [785]:
from torch.utils.data import DataLoader, Dataset, random_split
import torchaudio
from torchvision import transforms, utils
# ----------------------------
# Sound Dataset
# ----------------------------
class SongLabelSet(Dataset):
  def __init__(self, df):
    self.df = df

  # ----------------------------
  # Number of items in dataset
  # ----------------------------
  def __len__(self):
    return len(self.df)    
    
  # ----------------------------
  # Get i'th item in dataset
  # ----------------------------
  def __getitem__(self, idx):
    values = [
        self.df["acousticness"][idx],
        self.df["danceability"][idx],
        self.df["energy"][idx],
        self.df["instrumentalness"][idx],
        self.df["liveness"][idx],
        self.df["speechiness"][idx],
        self.df["valence"][idx],
    ]
    values = torch.tensor(values, dtype=torch.float32)
    label = self.df["cluster_id"][idx]
    label = torch.tensor(self.df["cluster_id"][idx])
    return values, label


In [786]:
songData = SongLabelSet(songDataset)

In [787]:
songData[1]

(tensor([0.7395, 0.6931, 0.5902, 0.3392, 0.1644, 0.1984, 0.6502]),
 tensor(18., dtype=torch.float64))

In [788]:
num_items = len(songDataset)
num_train = round(num_items * 0.8)
num_val = num_items - num_train
train_ds, val_ds = random_split(songData, [num_train, num_val])
num_items
len(val_ds)

10444

In [789]:
batch_size = 64

In [790]:
train_dl = torch.utils.data.DataLoader(train_ds, batch_size=batch_size, shuffle=True)
val_dl = torch.utils.data.DataLoader(val_ds, batch_size=batch_size, shuffle=False)

In [791]:
import torch
import torch.nn as nn

class LabelToClusterModel(nn.Module):
    def __init__(self):
        super(LabelToClusterModel, self).__init__()
        self.fc1 = nn.Linear(7, 128)
        self.relu1 = nn.ReLU()
        self.fc2 = nn.Linear(128, 256)
        self.relu2 = nn.ReLU()
        self.fc3 = nn.Linear(256, 512)
        self.relu3 = nn.ReLU()
        self.fc4 = nn.Linear(512, 500)
        self.softmax = nn.Softmax(dim=1)
        
        nn.init.xavier_uniform_(self.fc1.weight)
        nn.init.zeros_(self.fc1.bias)
        nn.init.xavier_uniform_(self.fc2.weight)
        nn.init.zeros_(self.fc2.bias)
        nn.init.xavier_uniform_(self.fc3.weight)
        nn.init.zeros_(self.fc3.bias)
        nn.init.xavier_uniform_(self.fc4.weight)
        nn.init.zeros_(self.fc4.bias)

    def forward(self, x):
        x = self.fc1(x)
        x = self.relu1(x)
        x = self.fc2(x)
        x = self.relu2(x)
        x = self.fc3(x)
        x = self.relu3(x)
        x = self.fc4(x)
        x = self.softmax(x)
        return x

In [792]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [799]:
model = LabelToClusterModel()
model.to(device)
optimizer = torch.optim.Adam(model.parameters(), lr=0.1)
criterion = nn.CrossEntropyLoss()
print(next(model.parameters()).device)

cuda:0


In [806]:
def trainLabel(model, optimizer, criterion, trainloader, testloader, num_epochs):
    model.train()
    lossList = []
    accuracyList = []
#     print(device)
    for epoch in range(num_epochs):
        train_loss = 0.0
        train_acc = 0.0
        val_loss = 0.0
        val_acc = 0.0
        for data in trainloader:
            
            inputs, labels = data
            inputs, labels = inputs.to(device), labels.to(device)
            labels = labels.type(torch.LongTensor)

            optimizer.zero_grad()

            outputs = model(inputs)
            predicted_class = torch.argmax(outputs, dim=1)
            print(predicted_class)
#             break
            loss = criterion(predicted_class.to(device), labels.to(device))
            loss.backward()
            optimizer.step()
            
            train_loss += loss.item()
            _, predicted = torch.max(outputs.data, 1)
            train_acc += (predicted == labels.to(device)).sum().item()
            

 # Validation loop
        with torch.no_grad():
            for inputs, labels in testloader:
                inputs, labels = inputs.to(device), labels.to(device)
                labels = labels.type(torch.LongTensor)

                outputs = model(inputs.to(device))
                loss = criterion(outputs.to(device), labels.to(device))
                
                val_loss += loss.item()
                _, predicted = torch.max(outputs.data, 1)
                val_acc += (predicted == labels.to(device)).sum().item()
        
        # Print epoch statistics
        train_loss /= len(trainloader.dataset)
        train_acc /= len(trainloader.dataset)
        val_loss /= len(testloader.dataset)
        val_acc /= len(testloader.dataset)
        print(f'Epoch {epoch+1}: Train Loss={train_loss:.4f}, Train Acc={train_acc:.4f}, Val Loss={val_loss:.4f}, Val Acc={val_acc:.4f}')

    print("Finished training")
    return lossList, accuracyList

In [807]:
lossList, accuracyList = trainLabel(model, optimizer, criterion, train_dl, val_dl, 50)

tensor([ 61,  21, 381, 330, 377, 330, 377, 474, 474, 381,  21, 377, 445, 377,
        474,  21, 330, 377, 377, 474, 377, 381, 474, 330, 377, 377, 474, 377,
        377, 377, 381, 381, 381, 474, 377, 377, 474, 377, 474, 377, 377, 330,
        377, 474, 381, 474, 377, 381,  21,  61, 474,  21, 377, 474, 393, 474,
        377, 330, 474, 377, 377, 381, 377, 381], device='cuda:0')


RuntimeError: Expected floating point type for target with class probabilities, got Long

In [808]:
# Define transform to normalize data
transform = transforms.Compose(
    [transforms.ToTensor(),
     transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))])

# Download and load training data
trainset = torchvision.datasets.CIFAR10(root='./data', train=True,
                                        download=True, transform=transform)
trainloader = torch.utils.data.DataLoader(trainset, batch_size=4,
                                          shuffle=True, num_workers=2)

# Download and load test data
testset = torchvision.datasets.CIFAR10(root='./data', train=False,
                                       download=True, transform=transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=4,
                                         shuffle=False, num_workers=2)

NameError: name 'torchvision' is not defined